<table width="100%">
    <tr style="border-bottom:solid 2pt #009EE3">
        <td class="header_buttons">
            <a href="synchronisation.zip" download><img src="../../images/icons/download.png" alt="biosignalsnotebooks | download button"></a>
        </td>
        <td class="header_buttons">
            <a href="https://mybinder.org/v2/gh/biosignalsplux/biosignalsnotebooks/mybinder_complete?filepath=biosignalsnotebooks_environment%2Fcategories%2FPre-Process%2Fsynchronisation.dwipynb" target="_blank"><img src="../../images/icons/program.png" alt="biosignalsnotebooks | binder server" title="Be creative and test your solutions !"></a>
        </td>
        <td></td>
        <td class="header_icons">
            <a href="../MainFiles/biosignalsnotebooks.ipynb"><img src="../../images/icons/home.png" alt="biosignalsnotebooks | home button"></a>
        </td>
        <td class="header_icons">
            <a href="../MainFiles/contacts.ipynb"><img src="../../images/icons/contacts.png" alt="biosignalsnotebooks | contacts button"></a>
        </td>
        <td class="header_icons">
            <a href="https://github.com/biosignalsplux/biosignalsnotebooks" target="_blank"><img src="../../images/icons/github.png" alt="biosignalsnotebooks | github button"></a>
        </td>
        <td class="header_logo">
            <img src="../../images/ost_logo.png" alt="biosignalsnotebooks | project logo">
        </td>
    </tr>
</table>

<link rel="stylesheet" href="../../styles/theme_style.css">
<!--link rel="stylesheet" href="../../styles/header_style.css"-->
<link rel="stylesheet" href="https://cdnjs.cloudflare.com/ajax/libs/font-awesome/4.7.0/css/font-awesome.min.css">

<table width="100%">
    <tr>
        <td id="image_td" width="15%" class="header_image_color_4"><div id="image_img"
        class="header_image_4"></div></td>
        <td class="header_text"> Device Synchronisation - Cable, Light and Sound Approaches </td>
    </tr>
</table>

<div id="flex-container">
    <div id="diff_level" class="flex-item">
        <strong>Difficulty Level:</strong>   <span class="fa fa-star checked"></span>
                                <span class="fa fa-star checked"></span>
                                <span class="fa fa-star checked"></span>
                                <span class="fa fa-star"></span>
                                <span class="fa fa-star"></span>
    </div>
    <div id="tag" class="flex-item-tag">
        <span id="tag_list">
            <table id="tag_list_table">
                <tr>
                    <td class="shield_left">Tags</td>
                    <td class="shield_right" id="tags">pre-process&#9729;light&#9729;sound&#9729;sync&#9729;correlation</td>
                </tr>
            </table>
        </span>
        <!-- [OR] Visit https://img.shields.io in order to create a tag badge-->
    </div>
</div>

When acquiring data with multiple devices, it may be difficult to start the acquisition at exactly the same instant. This means that events that start at exactly the same time, may appear to be delayed for signals of different devices.

Data processing and signal analysis may depend on the acquisition instants and the synchrony of different devices in order to understand the causes of different processes. For example,  when dealing with ECG data, recorded during the execution of physical exercise with variable intensity, it may be important to know the instants in which a difference of physical intensity take place, to match with the correct period of heartbeating.

In this <strong><span class="color5">Jupyter Notebook</span></strong>, two methods to synchronise signals will be explained using different triggers and sensors.

<strong>Note</strong>: For a high level explanation of how to synchronise signals, we recommend you to see the notebooks: 
<ul>
    <li><a href="synchrony_sound.ipynb">Synchrony - Acoustic Signal <img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></a> <!--strong><span class="color2">&gt;&gt; Future Release on 6th January 2020</span></strong--></li>
    <li><a href="synchrony_light.ipynb">Synchrony - Light Signal <img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></a> <!--strong><span class="color5">&gt;&gt; Future Release on 16th December 2019</span></strong--> </li>
    <li><a href="synchrony_acc.ipynb">Synchrony - Accelerometer Signal <img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></a> <!--strong><span class="color7">&gt;&gt; Future Release on 2nd December 2019</span></strong--> </li>
</ul>

<hr>

<p class="steps">1 - Import the required packages</p>
In order to facilitate our calculus, we will be using methods from the </span><strong><span class="color2">biosignalsnotebooks</span></strong> and <strong>numpy</strong> Python packages, that have several mathematical and auxiliary functions to ease our work.

In [1]:
# biosignalsnotebooks own package for loading and plotting the acquired data
import biosignalsnotebooks as bsnb

# Scientific packages
import numpy as np

<p style="font-size:20pt;color:#62C3EE;padding-bottom:5pt">Generic Synchronisation Example</p>

There are various methods that can be used in order to synchronise signals. We will show two of the most used techniques, one based on the definition of a threshold and one based on the analysis of the cross-correlation between two signals.<br>
Our methods can be applied to multiple sources of one-dimensional signals, such as ECG, EEG or accelerometer, thus, we will show how to use them with synthetic signals and then we will apply them to real signals acquired with two <strong><span class="color2">biosignalsplux</span></strong> devices.

<p class="steps">2 - Generate synthetic signals</p>

We will start by generating signals consisting of sine waves with the same period (frequency) and amplitude, but different phase.

In [2]:
# Generate a time axis (0 to 100 s with 10 Hz sampling rate)
t = np.arange(0,100,0.1)

# Generate two similar dephased signals
period = 2*np.pi/10
phase = np.pi/2
signal_1 = np.sin(period * t)
signal_2 = np.sin(period * t + phase)

In [3]:
bsnb.plot([t, t], [signal_1, signal_2])

The sampling frequency was defined to 10 Hz and the period was defined to 10 time units, thus each period of each signal is composed of 100 data points. The delay corresponds to $\frac{phase}{period}$ of the period of the signals, hence, is expected to be 2.5 time units, thus, 25 data points.

<p class="steps">3 - Synchronise signals using a threshold</p>
This method, may be viewed as a naive perspective due to the intuition that gives origin to it. It is assumed that both signals have identical behaviour and, then, equal values should be temporally aligned. Thus, by defining a threshold, we say that the moment when the two signals pass it, corresponds to a moment that should be aligned. 

First, we normalise the signals in order to have them in the same order of amplitude. In this case, we used the z-score normalisation, which results in signal with zero mean and unit variance.

In [4]:
# Normalise the first signal
m_signal_1 = signal_1 - np.mean(signal_1); w_signal_1 = m_signal_1 / np.std(m_signal_1)

# Normalise the second signal
m_signal_2 = signal_2 - np.mean(signal_2); w_signal_2 = m_signal_2 / np.std(m_signal_2)

For the threshold, we defined an absolute threshold to be applied to the normalised signals, but it could be a relative value, such as 80% of the maximum value of one of the normalised signals.

In [5]:
# Define the absolute value:
threshold = 0.8

# Defining a relative threshold, 80% of the maximum value of the first signal normalised:
# relative_threshold = 0.8 * np.max(w_signal_1)

After defining the threshold, we should align the signals by the first point in which the signals pass above that threshold. The opposite could also be done, align the signals by the point in which the signals pass from above to below the threshold.

In [6]:
# np.where function allows to get the values where each signal are higher than the threshold.
# Then, we just need to get the first index in which the signals pass the threshold, thus the indexing.
align_signal_1 = np.where(w_signal_1 > threshold)[0][0]
align_signal_2 = np.where(w_signal_2 > threshold)[0][0]

The values <strong>align_signal_1</strong> and <strong>align_signal_2</strong> are the respective first points where signal_1 and signal_2 surpass the threshold. Having the indexes of alignment, we can align the signals.

In [7]:
signal_1_aligned = signal_1[align_signal_1:]
signal_2_aligned = signal_2[align_signal_2:]

In [8]:
bsnb.plot([np.arange(len(signal_1_aligned)), np.arange(len(signal_2_aligned))], [signal_1_aligned, signal_2_aligned])

The signals did not end up synchronised. This is due to the difficulty of choosing a correct value for the threshold. If the threshold had been defined to 1.4, the results would improve as can be seen in the next figure. Nevertheless, this is an unexpensive computational method that may work in real time and when the threshold is well defined can present good results.

In [9]:
# Definition of the threshold.
threshold = 1.4

align_signal_1 = np.where(w_signal_1 > threshold)[0][0]
align_signal_2 = np.where(w_signal_2 > threshold)[0][0]

signal_1_aligned = signal_1[align_signal_1:]
signal_2_aligned = signal_2[align_signal_2:]

bsnb.plot([np.arange(len(signal_1_aligned)), np.arange(len(signal_2_aligned))], [signal_1_aligned, signal_2_aligned])

<p class="steps">4 - Synchronise signals using the full cross-correlation between two signals</p>

This is a more robust method that can not be applied in real time, but does not depend on the selection of parameters. It starts by calculating the full cross-correlation between two signals.<br>
Cross-correlation is a metric that allows to assess the similarity between two signals (<strong>f</strong> and <strong>g</strong>) by the displacement of one of the signals along the other. Mathematically it can be represented by:
\begin{equation}
    (f \star g)(n) = \sum_{m = -\infty}^{+ \infty} f(m) g(m+n)
\end{equation}
being $m$ the number of the sample under analysis, while $n$ defines the displacement/lag of <strong>g</strong> in relation to $f(m)$.

Once the signals are not infinite, computational systems compute the cross-correlation in instants where the signal is not defined by zero-padding the needed time instants, resulting in a correlation signal with length of the sum of both signals. The resulting correlation signal may be influenced by the zero-padding, but it is still possible to use this metric to calculate the dephasing of signals and it may be used to synchronise them.

Once again, we start by normalising the signals with the z-score normalisation technique.

In [10]:
# Normalise the signals using the z-score normalisation.
m_signal_1 = signal_1 - np.mean(signal_1); w_signal_1 = m_signal_1 / np.std(m_signal_1)
m_signal_2 = signal_2 - np.mean(signal_2); w_signal_2 = m_signal_2 / np.std(m_signal_2)

Fortunately, <strong>numpy</strong> has an implementation of the correlation function, so we will not need to program it ourselves. The application of this function only takes one step and allows to calculate the full cross-correlation between two signals, returning the resulting correlation signal.

In [11]:
# Calculate the full cross-correlation between the two signals.
correlation = np.correlate(w_signal_1, w_signal_2, 'full')

In [12]:
bsnb.plot(np.arange(len(correlation)), correlation)

As can be seen through the previous figure, the correlation signal increases as it reaches the centre and then decreases again. This is caused by the referred zero-padding, which does not contribute to the correlation of the two signals, resulting in "tails" with decreasing values starting from the points of full overlap (in fact, the size of those tails is equal to the length of the shorter signal).

In this case, once the signals are similar in length, the centre of the signal corresponds to the full overlap of the two signals, thus, if they were phased, the maximum value of the correlation signal, which corresponds to the instant of synchronisation of the signals, should correspond to the centre of the x axis.

In order to calculate the difference of phases, we can calculate the distance between the centre of the correlation signal and the instant in which occurs the maximum value.

In [13]:
# Finding the portion of the signal that does not belong to the tails. 
# This is done by subtracting the length of the shorter signal to length of the correlation signal. 
# In this case the signals have equal lengths, so it is enough to divide the correlation signal by two.
center = len(correlation)//2

# Finding the position of the maximum value of the correlation signal
max_position = correlation.argmax()

# Calculate the phase between the signals. The np.abs calculates the absolute value, assuring that the value is not negative.
phase = np.abs(center - max_position)

In [14]:
bsnb.plot([np.arange(len(signal_1[25:])), np.arange(len(signal_2))], [signal_1[25:], signal_2], legend=['signal_1', 'signal_2'])
print("Phase difference in data points: %d" % (phase))

Phase difference in data points: 25


The result shows that the usage of the cross-correlation allowed to calculate the correct dephasing between the two signals without the need to define any parameter.

<p class="steps">4.1 - Calculate the delay between two signals that generate specific correlation signals</p>

There are cases where the correlation signal presents a plateau at the maximum value, especially if the signals are not standardised. In these cases, the aforementioned method may result in a a phase value of 0 even when there is a delay.<br>
In this topic it will be shown one example that can generate such results and how to resolve them. This method is more generic than the previous one and can be used to all cases.

In [15]:
# Generate step signals that start with zeros and pass to ones at different moments.
x = np.concatenate([np.zeros(500), np.ones(500)]) 
y = np.concatenate([np.zeros(400), np.ones(600)])

In [16]:
time_axis = np.arange(0, 1000)
bsnb.plot([time_axis, time_axis], [x, y], legend=['x signal', 'y signal'])

As can be seen by the previous figure, the dephasing of the two signals is of 100 data points.

Next, we calculate the full cross-correlation between the two signals using the <strong>numpy</strong> Python package.

In [17]:
# Calculate the cross-correlation between the two signals
corr = np.correlate(x, y, 'full')

In [18]:
bsnb.plot(np.arange(len(corr)), corr)

The next cells correspond to the presentation of the more generic method to calculate the dephasing between two signals using the full cross-correlation. Similarly to the previous method, we will try to find the difference between the position of the maximum value and the positions corresponding to the full overlap between the two signals, that in this case, corresponds to the central data point of the correlation signal.

In [19]:
# Finding the centre of the signal
centre = len(corr)//2

# Finding the position of the maximum value of the signal
max_position = corr.argmax()

# Calculating the difference between the centre and the position of the maximum value
phase_straight = np.abs(centre - max_position)

The difference occurs now. We have found the position of the maximum value in the correlation signal and also the difference between that position and the full overlap of the two signals. Once there is a plateau that extends between the centre of the signal and the true dephasing between the signals, the result will be 0, because it is the first time that the maximum value appears, but it does not correspond to the true, as can be seen by the figure where we show the two signals.

Therefore, we should find the maximum value of the reversed correlation signal, that, in this case, would give us the real dephasing between the two signals.<br>
This step will give us the first point where the reversed correlation signal reaches the maximum value, that corresponds to the last point where the straight correlation signal reaches that value.

In [20]:
# Calculate the reversed correlation signal.
reversed_correlation_signal = corr[::-1]

# Finding the position of the maximum value of the reversed signal.
max_position_reversed = reversed_correlation_signal.argmax()

# Calculating the difference between the centre and the position of the maximum value in the reversed correlation signal
phase_reversed = np.abs(centre - max_position_reversed)

In order to calculate the true dephasing between the two signals, we should find the maximum dephasing between the calculated values - of the straight and the reversed correlation signals. Thus, we guarantee that we find the true dephasing between two signals independently of wich one is the delayed signal.<br>
<b>Note</b>: If the computation of the full cross-correlation was made in reverse, <strong>np.correlate(y, x, 'full')</strong>, the correlation signal would be mirrored and the previous method would give the true dephasing between the two signals, but we could still use the generic method due to this step.

In [21]:
# Calculate the dephasing between the signals. Maximum value of both 
# results guarantees that we find the true dephasing of the signals 
phase = np.max([phase_straight, phase_reversed])

In [22]:
print("Phase difference by the previous method: %d" % (phase_straight))
print("Phase difference by the new method: %d" % (phase))

Phase difference by the previous method: 0
Phase difference by the new method: 100


<p class="steps">5 - Synchronising the signals</p>

Finally, to synchronise both signals, we may crop one of the signals in order to align them by the most representative feature. In this case, the most representative feature is the step of both signals.

In [23]:
x = x[phase:]

In [24]:
bsnb.plot([np.arange(len(x)), np.arange(len(y))], [x, y], legend=['x signal', 'y signal'])

<p style="font-size:20pt;color:#62C3EE;padding-bottom:5pt">Demonstration using an acoustic signal</p>
This synchronisation method may be applied to generic cases. In this specific application, it was acquired an acoustic signal by two different <strong><span class="color2">biosignalsplux</span></strong> in the same room. The acquisitions did not start at same time, and so the signals are dephased by some seconds.

In order to validate the synchronisation approach, it was produced one distinctive event (clapping) that can help us to synchronise our signals. The idea is that, even if we did not know the difference in time between the start of the acquisition, we are certain that the clap was produced at the same instant for both devices.

<p class="steps">1 - Loading data from file</p>

In [25]:
# Load the first file
relative_path_sound = r"..\..\signal_samples\sync_acoustic_1.txt"
file_sound_1 = open(relative_path_sound)
# Store only the signal column
data_sound_1 = np.loadtxt(file_sound_1)[:,2]

# Load the second file
relative_path_sound = r"..\..\signal_samples\sync_acoustic_2.txt"
file_sound_2 = open(relative_path_sound)
# Store only the signal column
data_sound_2 = np.loadtxt(file_sound_2)[:,2]

In [26]:
bsnb.plot([np.arange(len(data_sound_1)), np.arange(len(data_sound_2))], [data_sound_1, data_sound_2], legend=['data_sound_1', 'data_sound_2'])

<p class="steps">2 - Calculating the dephasing and synchronising the signals</p>

<strong><span class="color2">biosignalsnotebooks</span></strong> package offers a function to automatically apply the synchronisation method described above that returns the dephasing between the input signals and the synchronised signals.

In [27]:
dephase_sound, data_sound_1, data_sound_2 = bsnb.synchronise_signals(data_sound_2, data_sound_1)

In [28]:
bsnb.plot([np.arange(len(data_sound_1)), np.arange(len(data_sound_2))], [data_sound_1, data_sound_2], legend=['data_sound_1', 'data_sound_2'])
print("The phase between the signals is: %d data points" % dephase_sound)

The phase between the signals is: 13198 data points


<p style="font-size:20pt;color:#62C3EE;padding-bottom:5pt">Demonstration using a light signal</p>
The next application consists of a light signal acquired by two different <strong><span class="color2">biosignalsplux</span></strong> hubs in the same room. The acquisitions did not start at same time, and so the signals are dephased by some seconds.<br>
The acquisition started with the light off and the distinctive event was to turn on the light. There are other events that could be used, for example, aim a flashlight at the sensors at a close distance or completely cover the sensors at the same time.

<p class="steps">1 - Loading data from file</p>

In [29]:
# Load the first file
relative_path_light = r"..\..\signal_samples\sync_light_1.txt"
file_light_1 = open(relative_path_light)
# Keep only the signal column
data_light_1 = np.loadtxt(file_light_1)[:,2]

# Load the second file
relative_path_light = r"..\..\signal_samples\sync_light_2.txt"
file_light_2 = open(relative_path_light)
# Keep only the signal column
data_light_2 = np.loadtxt(file_light_2)[:,2]

In [30]:
bsnb.plot([np.arange(len(data_light_1)), np.arange(len(data_light_2))], [data_light_1, data_light_2], legend=['data_light_1', 'data_light_2'])

Once again, we will use the function available in <strong><span class="color1">biosignalsnotebooks</span></strong> that allows to synchronise two signals in a direct way.

In [31]:
dephase_light, data_light_1, data_light_2 = bsnb.synchronise_signals(data_light_2, data_light_1)

In [32]:
bsnb.plot([np.arange(len(data_light_1)), np.arange(len(data_light_2))], [data_light_1, data_light_2], legend=['data_light_1', 'data_light_2'])
print("The phase between the signals is: %d data points" % dephase_light)

The phase between the signals is: 13664 data points


<p style="font-size:20pt;color:#62C3EE;padding-bottom:5pt">Demonstration using the synchronisation cable</p>

This is the simplest application. It is available a synchronisation cable, https://store.plux.info/cables/231-synchronization-cable.html, that is able to synchronise acquisitions made by multiple <strong><span class="color2">biosignalsplux</span></strong> devices in real time using <strong><span class="color2">OpenSignals</span></strong>. This cable is connected between the various devices and ensures that all devices start the acquisition at the same instant and guarantees the synchronisation throughout the acquisition.

<p class="steps">1 - Acquiring an acoustic signal sample</p>

The acquisitions consisted on clapping in different instants and will allow to calculate the precision of our synchronisation technique if compared to the result of the synchronisation cable, which is the ground truth.

In [33]:
# Load the file
relative_path_cable = r"..\..\signal_samples\sync_cable_acoustic.txt"
file_cable_1 = open(relative_path_cable)

txt = np.loadtxt(file_cable_1)
# First signal column
data_cable_1 = txt[:,2]
# Second signal column (in this case both signals were stored in the same file)
data_cable_2 = txt[:,5]

In [34]:
bsnb.plot([np.arange(len(data_cable_1)), np.arange(len(data_cable_2))], [data_cable_1, data_cable_2], legend=['data_cable_1', 'data_cable_2'])

As can be seen by the previous figure, the signals are synchronised without the application of our method, due to the utilisation of the synchronisation cable.

By calculating the dephasing between the two signals, we know the difference between our method and the ground truth. In order for our precision to be maximum, the calculated dephasing should be 0. The calculus of the dephasing is made by the application of the synchronise_signals function available in the <strong><span class="color2">biosignalsnotebooks</span></strong> package.

In [35]:
dephase_cable, data_cable_1, data_cable_2 = bsnb.synchronise_signals(data_cable_1, data_cable_2)

In [36]:
bsnb.plot([np.arange(len(data_cable_1)), np.arange(len(data_cable_2))], [data_cable_1, data_cable_2], legend=['data_cable_1', 'data_cable_2'])
print("The phase between the signals is: %d data points" % dephase_cable)

The phase between the signals is: 1 data points


The comparison between our method and the usage of the synchronisation technique revealed a difference of 1 data point. Since the sampling rate is 1000 Hz, the precision is $\frac{1}{1000} = $ 0.001 seconds.

<p class="steps">2 - Acquiring a light signal sample</p>

The same experience can be made using light sensors. Again, the experience consisted on the acquisition of the signal in a dark environment that, after a short period of time, was illuminated.

In [37]:
# Load the first file
relative_path_cable = r"..\..\signal_samples\sync_cable_light.txt"
file_cable_1 = open(relative_path_cable)

txt_light = np.loadtxt(file_cable_1)
# First signal column
light_cable_1 = txt_light[:,2]
# Second signal column (in this case both signals were stored in the same file)
light_cable_2 = txt_light[:,5]

In [38]:
bsnb.plot([np.arange(len(light_cable_1)), np.arange(len(light_cable_2))], [light_cable_1, light_cable_2], legend=['light_cable_1', 'light_cable_2'])

We use the same procedure as before in order to assess the quality of our synchronisation method, in which we use the <strong>synchronise_signals</strong> function available in the <strong><span class="color1">biosignalsnotebooks</span></strong> package.

In [39]:
dephase_cable, light_cable_1, light_cable_2 = bsnb.synchronise_signals(light_cable_1, light_cable_2)

In [40]:
bsnb.plot([np.arange(len(light_cable_1)), np.arange(len(light_cable_2))], [light_cable_1, light_cable_2], legend=['light_cable_1', 'light_cable_2'])
print("The phase between the signals is: %d data points" % dephase_cable)

The phase between the signals is: 0 data points


The comparison between our method and the usage of the synchronisation technique in this case revealed a difference of 0 data points and, thus, the precision reaches its maximum.

As can be seen from the last two experiments, this method of synchronisation works for signals with distinctive events, such as, clapping or turning on the light in a dark environment. This procedures could be performed to identify an occurrence in other signals.<br>

Time delays or asynchrony are very common when acquiring similar data with different devices, but as we demonstrated are easily solvable problems.<br>

<strong><span class="color7">We hope that you have enjoyed this guide. </span><span class="color2">biosignalsnotebooks</span><span class="color4"> is an environment in continuous expansion, so don't stop your journey and learn more with the remaining <a href="../MainFiles/biosignalsnotebooks.ipynb">Notebooks <img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></a></span></strong> ! 

<hr>
<table width="100%">
    <tr>
        <td class="footer_logo">
            <img src="../../images/ost_logo.png" alt="biosignalsnotebooks | project logo [footer]">
        </td>
        <td width="40%" style="text-align:left">
            <a href="../MainFiles/aux_files/biosignalsnotebooks_presentation.pdf" target="_blank">&#9740; Project Presentation</a>
            <br>
            <a href="https://github.com/biosignalsplux/biosignalsnotebooks" target="_blank">&#9740; GitHub Repository</a>
            <br>
            <a href="https://pypi.org/project/biosignalsnotebooks/" target="_blank">&#9740; How to install biosignalsnotebooks Python package ?</a>
            <br>
            <a href="https://www.biosignalsplux.com/notebooks/Categories/MainFiles/signal_samples.ipynb">&#9740; Signal Library</a>
        </td>
        <td width="40%" style="text-align:left">
            <a href="https://www.biosignalsplux.com/notebooks/Categories/MainFiles/biosignalsnotebooks.ipynb">&#9740; Notebook Categories</a>
            <br>
            <a href="https://www.biosignalsplux.com/notebooks/Categories/MainFiles/by_diff.ipynb">&#9740; Notebooks by Difficulty</a>
            <br>
            <a href="https://www.biosignalsplux.com/notebooks/Categories/MainFiles/by_signal_type.ipynb">&#9740; Notebooks by Signal Type</a>
            <br>
            <a href="https://www.biosignalsplux.com/notebooks/Categories/MainFiles/by_tag.ipynb">&#9740; Notebooks by Tag</a>
        </td>
    </tr>
</table>

In [41]:
from biosignalsnotebooks.__notebook_support__ import css_style_apply
css_style_apply()

.................... CSS Style Applied to Jupyter Notebook .........................


In [42]:
%%html
<script>
    // AUTORUN ALL CELLS ON NOTEBOOK-LOAD!
    require(
        ['base/js/namespace', 'jquery'],
        function(jupyter, $) {
            $(jupyter.events).on("kernel_ready.Kernel", function () {
                console.log("Auto-running all cells-below...");
                jupyter.actions.call('jupyter-notebook:run-all-cells-below');
                jupyter.actions.call('jupyter-notebook:save-notebook');
            });
        }
    );
</script>